In [33]:
import numpy as np
import pandas as pd
import json
import time
from pathlib import Path
from typing import Dict, List, Tuple, Any
from sklearn.experimental import enable_iterative_imputer
from sklearn.impute import IterativeImputer, KNNImputer, SimpleImputer
from sklearn.cross_decomposition import PLSRegression
from sklearn.model_selection import ParameterGrid, TimeSeriesSplit
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_squared_error, r2_score, mean_absolute_percentage_error
from sklearn.neighbors import KNeighborsRegressor
from sklearn.ensemble import GradientBoostingRegressor, RandomForestRegressor, StackingRegressor
from sklearn.linear_model import ElasticNet, Ridge, Lasso
from sklearn.svm import SVR
from sklearn.neural_network import MLPRegressor
from sklearn.base import clone
from xgboost import XGBRegressor


In [ ]:
def preprocess_sequences(
    df: pd.DataFrame,
    time_col: str = "Data",
    freq_hours: int = 6,
    col_validar: str | None = None,
    valor_invalido: int = -1,
) -> pd.DataFrame:
    """
    Preprocessa o DataFrame para identificar sequências contínuas no tempo e valores válidos.
    """
    df = df.copy()
    df[time_col] = pd.to_datetime(df[time_col])
    df = df.sort_values(time_col).reset_index(drop=True)

    if col_validar:
        df["valido"] = df[col_validar] != valor_invalido
    else:
        df["valido"] = True

    df["diff_h"] = df[time_col].diff().dt.total_seconds() / 3600
    df["nova_seq"] = (df["diff_h"] != freq_hours) | (~df["valido"])
    df["seq_id"] = df["nova_seq"].cumsum()

    return df

def get_largest_sequence(df: pd.DataFrame) -> pd.DataFrame:
    """
    Retorna o maior grupo contínuo de valores válidos (PARA BASELINES).
    """
    df = df.copy()

    df["valid_group"] = (df["valido"] != df["valido"].shift()).cumsum()
    valid_groups = df[df["valido"]].groupby("valid_group")

    if valid_groups.ngroups == 0:
        print("[WARN] Nenhuma sequência válida encontrada.")
        return pd.DataFrame()

    largest_group_id = valid_groups.size().idxmax()
    largest_seq_df = df[df["valid_group"] == largest_group_id].copy()

    largest_seq_df["orig_index"] = largest_seq_df.index + 2
    largest_seq_df.reset_index(drop=True, inplace=True)

    cols_to_drop = [c for c in ["valido", "diff_h", "nova_seq", "seq_id", "valid_group"] if c in largest_seq_df.columns]
    largest_seq_df.drop(columns=cols_to_drop, inplace=True)

    return largest_seq_df

def get_complete_sequence_stacking(df: pd.DataFrame, target_col: str = "Vazao_BBR") -> pd.DataFrame:
    """
    Retorna TODOS os dados válidos (PARA STACKING) - remove apenas linhas com valor inválido.
    """
    df_complete = df.copy()
    
    # Manter apenas linhas onde o target é válido
    df_complete = df_complete[df_complete[target_col] != -1].reset_index(drop=True)
    
    print(f"[STACKING] Dataset completo: {len(df_complete)} amostras válidas")
    return df_complete

def pipeline_preprocess_baselines(
    df: pd.DataFrame,
    time_col: str = "Data",
    freq_hours: int = 6,
    col_validar: str | None = None,
    valor_invalido: int = -1,
    n_std: int = 3
) -> pd.DataFrame:
    """
    Pipeline completa de preprocessamento:
    1. Identifica sequências contínuas
    2. Extrai a maior sequência válida
    3. Remove outliers
    """
    df_seq = preprocess_sequences(df, time_col, freq_hours, col_validar, valor_invalido)
    df_largest = get_largest_sequence(df_seq)

    if df_largest.empty:
        print("[WARN] DataFrame resultante está vazio após extração da maior sequência.")
        return df_largest

    return df_largest

In [35]:
# ========== FUNÇÕES DE MASCARAMENTO E TRANSFORMAÇÃO ==========

def apply_mask(df: pd.DataFrame, test_fraction: float = 0.2, seed_data: int = None) -> pd.DataFrame:
    """
    Aplica máscara sem seed fixa para avaliação única.
    CORREÇÃO: Garante que a máscara é aplicada corretamente.
    """
    df = df.copy()
    df["mask_applied"] = 0
    test_size = max(1, int(test_fraction * len(df)))  # Garante pelo menos 1 amostra
    
    # Usar seed aleatória ou fixa para reprodutibilidade
    if seed_data is not None:
        np.random.seed(seed_data)
    
    mask_indices = np.random.choice(df.index, size=test_size, replace=False)
    df.loc[mask_indices, "mask_applied"] = 1
    
    print(f"      Máscara: {test_size}/{len(df)} amostras ({test_fraction*100}%)")
    
    return df

def apply_mask_for_stacking(df: pd.DataFrame, test_fraction: float = 0.2, seed_data: int = None) -> pd.DataFrame:
    """
    Aplica máscara para avaliação do stacking - cria mask_applied.
    """
    df = df.copy()
    df["mask_applied"] = 0
    test_size = int(test_fraction * len(df))
    
    # Usar seed aleatória ou None
    rng = np.random.default_rng(seed=seed_data)
    mask_indices = rng.choice(df.index, size=test_size, replace=False)
    df.loc[mask_indices, "mask_applied"] = 1
    
    return df


def impute_values(
    df: pd.DataFrame,
    coluna_original="Vazao_BBR",
    coluna_nova="Feature_vazao_BBR",
    method="knn",
    n_neighbors=3,
    seed=42
) -> pd.DataFrame:
    """
    Versão robusta que cria mask_applied se não existir.
    """
    df = df.copy()

    # CORREÇÃO: Criar mask_applied se não existir
    # if "mask_applied" not in df.columns:
    #     print("    [INFO] Criando coluna 'mask_applied' para imputação...")
    #     df["mask_applied"] = 0  # Por padrão, nenhum valor é mascarado

    df[coluna_nova] = df[coluna_original]
    mask_indices = df[df["mask_applied"] == 1].index

    if len(mask_indices) == 0:
        return df

    df.loc[mask_indices, coluna_nova] = np.nan

    features_impute = ["Atraso(ms)", "Hop_count", coluna_nova]
    impute_data = df[features_impute].copy()

    method = method.lower()
    if method == "knn":
        imputer = KNNImputer(n_neighbors=n_neighbors)
    elif method in ["mean", "median"]:
        strategy = "mean" if method == "mean" else "median"
        imputer = SimpleImputer(strategy=strategy)
    elif method == "mice":
        imputer = IterativeImputer(random_state=seed)
    else:
        raise ValueError(f"Método '{method}' não suportado. Use 'knn', 'mean', 'median' ou 'mice'.")

    df[[coluna_nova]] = imputer.fit_transform(impute_data)[:, 2].reshape(-1, 1)

    return df

def add_rolling_features(df: pd.DataFrame, coluna_original="Vazao_BBR", window=3) -> pd.DataFrame:
    """
    Rolling features CORRIGIDA para evitar vazamento.
    """
    df = df.copy()
    
    df[f"{coluna_original}_rolling_mean"] = df[coluna_original].shift(1).rolling(window=window-1, min_periods=1).mean()
    df[f"{coluna_original}_rolling_std"] = df[coluna_original].shift(1).rolling(window=window-1, min_periods=1).std()
    
    return df

def engineer_features(df: pd.DataFrame, coluna_nova: str = "Feature_vazao_BBR") -> pd.DataFrame:
    """
    Feature engineering SEM data leakage - MESMO NOME.
    """
    df = df.copy()

    df["Atraso_log"] = np.log1p(df["Atraso(ms)"].clip(lower=0))
    df["Hop_inv"] = 1 / (df["Hop_count"] + 1)
    df["Atraso_x_Hop"] = df["Atraso(ms)"] * df["Hop_count"]
    df["Atraso_sq"] = df["Atraso(ms)"] ** 2
    
    df["Efficiency"] = df[coluna_nova] / ((df["Atraso(ms)"] + 1) * (df["Hop_count"] + 1))

    # Features temporais (se coluna Data existir)
    # if 'Data' in df.columns:
    #     try:
    #         df['Data'] = pd.to_datetime(df['Data'])
    #         df['dia_semana'] = df['Data'].dt.dayofweek
    #         df['mes'] = df['Data'].dt.month
    #         df['trimestre'] = df['Data'].dt.quarter
    #         df['semana_ano'] = df['Data'].dt.isocalendar().week
    #     except:
    #         pass

    # Features de lag (seguras)
    df["Vazao_lag1"] = df[coluna_nova].shift(1)
    df["Vazao_lag2"] = df[coluna_nova].shift(2)
    
    # Rolling features CORRIGIDAS - usar shift para evitar vazamento
    df["Vazao_roll_mean_3"] = df[coluna_nova].shift(1).rolling(window=2, min_periods=1).mean()
    df["Vazao_roll_std_3"] = df[coluna_nova].shift(1).rolling(window=2, min_periods=1).std()
    
    # Features de variação (seguras)
    df["Vazao_diff"] = df[coluna_nova].diff().fillna(0)
    df["Vazao_pct_change"] = df[coluna_nova].pct_change().fillna(0)
    
    # Features de interação (seguras)
    df["Vazao_div_Atraso"] = df[coluna_nova] / (df["Atraso(ms)"] + 1)
    df["Vazao_div_Hops"] = df[coluna_nova] / (df["Hop_count"] + 1)
    df["Vazao_x_Atraso"] = df[coluna_nova] * df["Atraso(ms)"]
    df["Vazao_x_Hops"] = df[coluna_nova] * df["Hop_count"]
    
    # Transformações da target (seguras)
    df["Vazao_log"] = np.log1p(df[coluna_nova].clip(lower=0))
    df["Vazao_sq"] = df[coluna_nova] ** 2
    df["Vazao_sqrt"] = np.sqrt(df[coluna_nova].clip(lower=0))

    for col in df.select_dtypes(include=[np.number]).columns:
        if df[col].isna().any():
            if col in ['Vazao_lag1', 'Vazao_lag2', 'Vazao_roll_mean_3', 'Vazao_roll_std_3']:
                df[col] = df[col].fillna(0)  # Preencher com 0 para features temporais
            else:
                df[col] = df[col].fillna(df[col].median())

    return df

def transform(
    df: pd.DataFrame,
    coluna_original="Vazao_BBR",
    coluna_nova="Feature_vazao_BBR",
    method="knn",
    n_neighbors=3,
    seed=42,
) -> pd.DataFrame:
    """
    Versão robusta que lida com ausência de mask_applied.
    """
    # # CORREÇÃO: Criar mask_applied se não existir
    # if "mask_applied" not in df.columns:
    #     df = df.copy()
    #     df["mask_applied"] = 0

    df = impute_values(df, coluna_original, coluna_nova, method, n_neighbors, seed)
    df = add_rolling_features(df, coluna_original, window=3)
    df = engineer_features(df, coluna_nova)
    return df


def transform_imputation(
    df: pd.DataFrame,
    coluna_original="Vazao_BBR",
    coluna_nova="Feature_vazao_BBR",
    method="median"
) -> pd.DataFrame:
    """
    Versão da transform adaptada para imputação - não requer mask_applied.
    """
    df = df.copy()

    # Criar coluna nova e identificar valores para imputar
    df[coluna_nova] = df[coluna_original]
    
    # Identificar valores que precisam ser imputados (-1 ou NaN)
    mask_imputar = (df[coluna_nova] == -1) | (df[coluna_nova].isna())
    
    if mask_imputar.sum() > 0:
        # Marcar valores para imputação como NaN
        df.loc[mask_imputar, coluna_nova] = np.nan

        features_impute = ["Atraso(ms)", "Hop_count", coluna_nova]
        impute_data = df[features_impute].copy()

        method = method.lower()
        if method == "knn":
            imputer = KNNImputer(n_neighbors=3)
        elif method in ["mean", "median"]:
            strategy = "mean" if method == "mean" else "median"
            imputer = SimpleImputer(strategy=strategy)
        elif method == "mice":
            imputer = IterativeImputer(random_state=42)
        else:
            raise ValueError(f"Método '{method}' não suportado. Use 'knn', 'mean', 'median' ou 'mice'.")

        df[[coluna_nova]] = imputer.fit_transform(impute_data)[:, 2].reshape(-1, 1)

    # Adicionar rolling features
    df = add_rolling_features(df, coluna_original, window=3)
    
    # Engineer features
    df = engineer_features(df, coluna_nova)
    
    return df



In [36]:
# ========== FUNÇÕES DE AVALIAÇÃO BASELINE ==========

def calculate_metrics(y_true, y_pred) -> Dict[str, Any]:
    """
    Calcula métricas de regressão (rmse, nrmse, r2, mape).
    """
    rmse = float(np.sqrt(mean_squared_error(y_true, y_pred)))
    nrmse = (rmse / y_true.mean()) * 100
    rmse = rmse / 1_000_000  # Normalizar para milhões
    r2 = r2_score(y_true, y_pred)
    if np.isnan(r2):
        r2 = None
    mape = float(mean_absolute_percentage_error(y_true, y_pred) * 100)

    return {
        "rmse": round(rmse, 2),
        "nrmse": round(nrmse, 2),
        "r2": r2 if r2 is not None else None,
        "mape": round(mape, 2)
    }

def run_baseline_evaluation(df: pd.DataFrame, value_col='Vazao_BBR', mask_col='mask_applied'):
    """
    Avalia múltiplos métodos de imputação baseline e retorna métricas completas.
    """
    if mask_col not in df.columns:
        raise ValueError(f"Coluna '{mask_col}' não encontrada no DataFrame.")

    results = {}

    df_eval = df[[value_col, mask_col]].copy()
    mask_indices = df_eval[df_eval[mask_col] == 1].index

    # Guardar valores originais
    df_eval['original'] = df_eval[value_col]
    # Aplicar máscara (transformar em NaN)
    df_eval.loc[mask_indices, value_col] = np.nan

    # ========== MÉDIA ==========
    df_mean = df_eval.copy()
    df_mean[value_col] = df_mean[value_col].fillna(df_mean[value_col].mean())
    results['Mean'] = calculate_metrics(
        df_eval['original'].loc[mask_indices], 
        df_mean[value_col].loc[mask_indices]
    )

    # ========== MEDIANA ==========
    df_median = df_eval.copy()
    df_median[value_col] = df_median[value_col].fillna(df_median[value_col].median())
    results['Median'] = calculate_metrics(
        df_eval['original'].loc[mask_indices], 
        df_median[value_col].loc[mask_indices]
    )

    # ========== KNN IMPUTER ==========
    try:
        df_knn = df_eval.copy()
        imputer = KNNImputer(n_neighbors=4)
        df_knn[value_col] = imputer.fit_transform(df_knn[[value_col]])
        results['KNNImputer'] = calculate_metrics(
            df_eval['original'].loc[mask_indices], 
            df_knn[value_col].loc[mask_indices]
        )
    except Exception as e:
        print(f"[ERRO] KNNImputer falhou: {e}")
        results['KNNImputer'] = {
            "rmse": None, 
            "nrmse": None, 
            "r2": None, 
            "mape": None
        }

    # ========== FORWARD FILL ==========
    df_ffill = df_eval.copy()
    df_ffill[value_col] = df_ffill[value_col].ffill().bfill()
    results['ForwardFill'] = calculate_metrics(
        df_eval['original'].loc[mask_indices], 
        df_ffill[value_col].loc[mask_indices]
    )

    # ========== BACKWARD FILL ==========
    df_bfill = df_eval.copy()
    df_bfill[value_col] = df_bfill[value_col].bfill().ffill()
    results['BackwardFill'] = calculate_metrics(
        df_eval['original'].loc[mask_indices], 
        df_bfill[value_col].loc[mask_indices]
    )

    # ========== ROLLING MEAN (janela=3) ==========
    df_rolling = df_eval.copy()
    window_size = 3
    df_rolling[value_col] = df_rolling[value_col].rolling(window=window_size, min_periods=1).mean()
    df_rolling[value_col] = df_rolling[value_col].ffill().bfill()  # Preenche NaNs restantes
    results['RollingMean'] = calculate_metrics(
        df_eval['original'].loc[mask_indices], 
        df_rolling[value_col].loc[mask_indices]
    )

    # ========== INTERPOLAÇÃO LINEAR ==========
    df_linear = df_eval.copy()
    df_linear[value_col] = df_linear[value_col].interpolate(method='linear').ffill().bfill()
    results['LinearInterpolation'] = calculate_metrics(
        df_eval['original'].loc[mask_indices], 
        df_linear[value_col].loc[mask_indices]
    )

    return results

In [37]:
# ========== FUNÇÕES DO STACKING OTIMIZADAS ==========

def calculate_metrics_stacking(y_true: np.ndarray, y_pred: np.ndarray, model_name: str, source: str):
    """
    Calcula métricas de forma robusta, tratando valores inválidos.
    """
    # Garantir que os arrays são numpy e têm o mesmo comprimento
    y_true = np.array(y_true).flatten()
    y_pred = np.array(y_pred).flatten()
    
    # Remover NaNs e infinitos
    mask = ~(np.isnan(y_true) | np.isnan(y_pred) | np.isinf(y_true) | np.isinf(y_pred))
    
    if mask.sum() == 0:
        return {
            "rmse": None,
            "nrmse": None, 
            "r2": None,
            "mape": None
        }
    
    y_true_clean = y_true[mask]
    y_pred_clean = y_pred[mask]
    
    if len(y_true_clean) < 2:
        return {
            "rmse": None,
            "nrmse": None,
            "r2": None,
            "mape": None
        }
    
    try:
        rmse = np.sqrt(mean_squared_error(y_true_clean, y_pred_clean))
        nrmse = (rmse / (np.mean(y_true_clean) + 1e-8)) * 100
        rmse_normalized = rmse / 1_000_000
        
        r2 = r2_score(y_true_clean, y_pred_clean)
        r2 = r2 if not np.isnan(r2) else None
        
        # MAPE com proteção contra divisão por zero
        mape = np.mean(np.abs((y_true_clean - y_pred_clean) / (np.abs(y_true_clean) + 1e-8))) * 100
        
        return {
            "rmse": round(rmse_normalized, 2),
            "nrmse": round(nrmse, 2),
            "r2": r2,
            "mape": round(mape, 2)
        }
    except Exception as e:
        print(f"    ⚠️ Erro cálculo métricas {model_name}: {e}")
        return {
            "rmse": None,
            "nrmse": None,
            "r2": None,
            "mape": None
        }

def remove_nan_features(X: np.ndarray, feature_names: List[str]):
    """
    Remove features com NaN de forma mais robusta.
    """
    if len(X) == 0:
        return X, feature_names
        
    # Encontrar colunas sem NaN
    valid_indices = []
    for i, col in enumerate(feature_names):
        col_data = X[:, i]
        if not np.any(np.isnan(col_data)) and not np.all(np.isinf(col_data)):
            valid_indices.append(i)
    
    X_clean = X[:, valid_indices]
    feature_names_clean = [feature_names[i] for i in valid_indices]
    
    print(f"    📊 Features: {len(feature_names)} → {len(feature_names_clean)} (após remoção de NaN)")
    
    return X_clean, feature_names_clean

def train_base_models(X_train_scaled, y_train_scaled, X_test_scaled, y_test, scaler_y, feature_names: List[str], source: str):
    """
    Treina modelos base com validação cruzada temporal e hiperparâmetros otimizados.
    """
    base_models = {}
    best_params_list = {}

    # Limpar features com NaN
    X_train_scaled, features_clean = remove_nan_features(X_train_scaled, feature_names)
    X_test_scaled = X_test_scaled[:, [feature_names.index(f) for f in features_clean]]

    # Configurações otimizadas para séries temporais
    models = {
        "XGBRegressor": {
            "model": XGBRegressor(random_state=42, tree_method='hist', device='cpu', verbosity=0),
            "params": {
                'n_estimators': [100, 200],
                'learning_rate': [0.05, 0.1],
                'max_depth': [3, 5],
                'subsample': [0.8, 0.9],
                'colsample_bytree': [0.8, 1.0]
            }
        },
        "RandomForestRegressor": {
            "model": RandomForestRegressor(random_state=42, n_jobs=-1),
            "params": {
                'n_estimators': [100, 200],
                'max_depth': [10, 20],
                'min_samples_split': [2, 5],
                'min_samples_leaf': [1, 2]
            }
        },
        "GradientBoostingRegressor": {
            "model": GradientBoostingRegressor(random_state=42),
            "params": {
                'n_estimators': [100, 200],
                'learning_rate': [0.05, 0.1],
                'max_depth': [3, 5],
                'subsample': [0.8, 1.0]
            }
        },
        "KNeighborsRegressor": {
            "model": KNeighborsRegressor(n_jobs=4),
            "params": {
                'n_neighbors': [3, 5],
                'weights': ['uniform', 'distance'],
                'p': [1, 2]
            }
        },
        "ElasticNet": {
            "model": Pipeline([
                ('scaler', StandardScaler()),
                ('regressor', ElasticNet(random_state=42, max_iter=5000))
            ]),
            "params": {
                'regressor__alpha': [0.01, 0.1, 1.0],
                'regressor__l1_ratio': [0.3, 0.5, 0.7]
            }
        }
    }

    for name, info in models.items():
        print(f"    🔧 Otimizando {name}...")
        best_score = float('inf')
        best_model = None
        best_params = None

        # Ajustar n_neighbors para KNN baseado no tamanho dos dados
        if name == "KNeighborsRegressor":
            n_samples = X_train_scaled.shape[0]
            max_neighbors = min(10, n_samples - 1)
            info["params"]["n_neighbors"] = [min(n, max_neighbors) for n in info["params"]["n_neighbors"]]

        for params in list(ParameterGrid(info["params"]))[:8]:  # Limitar combinações
            try:
                model = clone(info["model"])
                model.set_params(**params)
                
                # Validação cruzada temporal
                n_splits = min(4, X_train_scaled.shape[0] // 3)
                if n_splits >= 2:
                    tscv = TimeSeriesSplit(n_splits=n_splits)
                    cv_scores = []
                    
                    for train_idx, val_idx in tscv.split(X_train_scaled):
                        X_train_cv, X_val_cv = X_train_scaled[train_idx], X_train_scaled[val_idx]
                        y_train_cv, y_val_cv = y_train_scaled[train_idx], y_train_scaled[val_idx]
                        
                        model.fit(X_train_cv, y_train_cv.ravel())
                        pred_val = model.predict(X_val_cv)
                        
                        # Calcular RMSE nos dados originais
                        y_val_original = scaler_y.inverse_transform(y_val_cv.reshape(-1, 1)).ravel()
                        pred_val_original = scaler_y.inverse_transform(pred_val.reshape(-1, 1)).ravel()
                        rmse = np.sqrt(mean_squared_error(y_val_original, pred_val_original))
                        cv_scores.append(rmse)
                    
                    avg_rmse = np.mean(cv_scores)
                else:
                    # Fallback: treinar e avaliar direto
                    model.fit(X_train_scaled, y_train_scaled.ravel())
                    pred_test = scaler_y.inverse_transform(
                        model.predict(X_test_scaled).reshape(-1, 1)
                    ).ravel()
                    avg_rmse = np.sqrt(mean_squared_error(y_test, pred_test))
                
                if avg_rmse < best_score:
                    best_score = avg_rmse
                    best_model = clone(model)
                    best_model.fit(X_train_scaled, y_train_scaled.ravel())
                    best_params = params
                    
            except Exception as e:
                continue

        if best_model is not None:
            base_models[name] = best_model
            best_params_list[name] = {"params": best_params, "rmse": best_score}
            print(f"    ✅ {name} - RMSE: {best_score/1_000_000:.2f}M")

    return base_models, best_params_list, features_clean

def train_stacking_model(base_models, X_train_scaled, y_train_scaled, X_test_scaled, y_test, scaler_y, source: str):
    """
    Stacking melhorado com meta-features e meta-modelos robustos.
    """
    if not base_models:
        print("    ⚠️ Nenhum modelo base disponível para stacking")
        return None, float('inf'), "None"
    
    base_models_list = [(name, model) for name, model in base_models.items() if model is not None]
    
    if not base_models_list:
        print("    ⚠️ Nenhum modelo base válido para stacking")
        return None, float('inf'), "None"

    # Criar meta-features
    def create_meta_features(models, X):
        meta_features = []
        for name, model in models:
            try:
                pred = model.predict(X)
                # Adicionar predição e "confidence" (distância da média)
                pred_normalized = (pred - pred.mean()) / (pred.std() + 1e-8)
                meta_features.extend([pred, pred_normalized])
            except:
                meta_features.extend([np.zeros(len(X)), np.zeros(len(X))])
        return np.column_stack(meta_features) if meta_features else X

    # Criar datasets com meta-features
    X_train_meta = create_meta_features(base_models_list, X_train_scaled)
    X_test_meta = create_meta_features(base_models_list, X_test_scaled)
    
    # Combinar com features originais
    X_train_stacked = np.column_stack([X_train_scaled, X_train_meta])
    X_test_stacked = np.column_stack([X_test_scaled, X_test_meta])

    # Meta-modelos otimizados
    final_estimators = {
        "Ridge": Ridge(alpha=1.0),
        "ElasticNet": ElasticNet(alpha=0.1, l1_ratio=0.5, random_state=42, max_iter=5000),
        "XGB": XGBRegressor(
            n_estimators=100, max_depth=3, learning_rate=0.1,
            random_state=42, verbosity=0
        )
    }

    best_model = None
    best_rmse = float('inf')
    best_name = ""

    for name, final_estimator in final_estimators.items():
        try:
            stacking = StackingRegressor(
                estimators=base_models_list,
                final_estimator=final_estimator,
                passthrough=True,
                n_jobs=-1,
                cv=min(3, X_train_scaled.shape[0] // 2)
            )
            
            stacking.fit(X_train_scaled, y_train_scaled.ravel())
            pred = scaler_y.inverse_transform(
                stacking.predict(X_test_scaled).reshape(-1, 1)
            ).ravel()
            
            rmse = np.sqrt(mean_squared_error(y_test, pred)) / 1_000_000
            
            if rmse < best_rmse:
                best_rmse = rmse
                best_model = stacking
                best_name = name
                
        except Exception as e:
            print(f"    ⚠️ Erro no meta-modelo {name}: {e}")
            continue

    if best_model is not None:
        print(f"    🎯 Stacking ({best_name}) - RMSE: {best_rmse:.2f}M")
    else:
        print("    ❌ Stacking falhou com todos os meta-modelos")

    return best_model, best_rmse, best_name

def predict_models(base_models, stacking_model, X_test_scaled, scaler_y):
    predictions = {}
    for name, model in base_models.items():
        pred = scaler_y.inverse_transform(model.predict(X_test_scaled).reshape(-1,1)).ravel()
        predictions[name] = pred

    if stacking_model is not None:
        pred = scaler_y.inverse_transform(stacking_model.predict(X_test_scaled).reshape(-1,1)).ravel()
        predictions["StackingRegressor"] = pred

    return predictions

def split_data(
    df: pd.DataFrame,
    features: List[str],
    target: str,
    mask_col: str = 'mask_applied'
) -> Tuple[
    pd.DataFrame, pd.DataFrame, pd.Series, pd.Series,
    np.ndarray, np.ndarray, np.ndarray, np.ndarray,
    StandardScaler, pd.Index, pd.Index, pd.DataFrame
]:
    """
    Separa dados em treino/teste baseado na máscara e aplica normalização.
    """
    if mask_col not in df.columns:
        raise ValueError(f"Coluna de máscara '{mask_col}' não encontrada no DataFrame.")

    df_ = df.copy()

    # Índices de treino e teste
    test_idx = df_[df_[mask_col] == 1].index
    train_idx = df_[df_[mask_col] == 0].index

    # Criar coluna mask_applied explícita (garante consistência)
    df_['mask_applied'] = 0
    df_.loc[test_idx, 'mask_applied'] = 1

    # Separação train/test
    X_train = df_.loc[train_idx, features]
    X_test = df_.loc[test_idx, features]

    y_train = df_.loc[train_idx, target]
    y_test = df_.loc[test_idx, target]

    # Escalonamento das features
    scaler_X = StandardScaler()
    X_train_scaled = scaler_X.fit_transform(X_train)
    X_test_scaled = scaler_X.transform(X_test)

    # Escalonamento do target
    scaler_y = StandardScaler()
    y_train_scaled = scaler_y.fit_transform(y_train.values.reshape(-1, 1))
    y_test_scaled = scaler_y.transform(y_test.values.reshape(-1, 1))

    return (
        X_train, X_test, y_train, y_test,
        X_train_scaled, X_test_scaled,
        y_train_scaled, y_test_scaled,
        scaler_y, train_idx, test_idx, df_
    )

In [38]:
# ========== NOVA LÓGICA DE AVALIAÇÃO ==========

def evaluate_baselines_single_run(df_largest: pd.DataFrame, fractions: list, target: str = "Vazao_BBR"):
    """
    Avalia baselines UMA VEZ para cada fração usando a maior sequência.
    """
    baseline_results = {}
    
    for frac in fractions:
        print(f"  [BASELINE] Fração {frac}")
        
        # Aplicar máscara uma vez (sem seed fixa)
        df_masked = apply_mask(df_largest, test_fraction=frac, seed_data=None)
        
        # Avaliar baselines
        baseline_metrics = run_baseline_evaluation(df_masked, value_col=target, mask_col='mask_applied')
        baseline_results[str(frac)] = baseline_metrics
    
    return baseline_results

def calculate_average_metrics(metrics_list):
    """Calcula média das métricas entre folds."""
    avg_metrics = {}
    
    for metric in ["rmse", "nrmse", "r2", "mape"]:
        values = [m[metric] for m in metrics_list if m[metric] is not None]
        if values:
            avg_metrics[metric] = round(np.mean(values), 2)
        else:
            avg_metrics[metric] = None
    
    return avg_metrics


def transform_for_evaluation(
    df: pd.DataFrame,
    coluna_original="Vazao_BBR",
    coluna_nova="Feature_vazao_BBR",
    method="median"
) -> pd.DataFrame:
    """
    Versão da transform para avaliação - CORRIGIDA para evitar vazamento.
    """
    df = df.copy()

    # Simplesmente copiar a coluna para feature engineering
    df[coluna_nova] = df[coluna_original]
    
    # Adicionar rolling features básicas (seguras)
    df = add_rolling_features(df, coluna_original, window=3)
    
    # Engineer features CORRIGIDA
    df = engineer_features(df, coluna_nova)
    
    return df

def stacking_cross_validation(df_complete: pd.DataFrame, test_fraction: float, target: str, n_splits: int = 5):
    """
    Executa validação cruzada para o stacking no dataset completo.
    """
    all_metrics = []
    
    # Preparar features usando a nova função
    df_transformed = transform_for_evaluation(
        df=df_complete,
        coluna_original=target,
        coluna_nova=f"Feature_{target}",
        method="median"
    )
    
    # Features para modelo
    exclude_cols = {target, "Data", "mask_applied"}
    features = [c for c in df_transformed.columns if c not in exclude_cols]
    
    X = df_transformed[features].fillna(0)
    y = df_transformed[target]
    
    # Validação cruzada temporal
    tscv = TimeSeriesSplit(n_splits=min(n_splits, len(df_complete) // 2))
    
    for fold, (train_idx, test_idx) in enumerate(tscv.split(X)):
        print(f"    Fold {fold + 1}/{tscv.n_splits}")
        
        try:
            # Separar dados
            X_train, X_test = X.iloc[train_idx], X.iloc[test_idx]
            y_train, y_test = y.iloc[train_idx], y.iloc[test_idx]
            
            # Escalar dados
            scaler_X = StandardScaler()
            X_train_scaled = scaler_X.fit_transform(X_train)
            X_test_scaled = scaler_X.transform(X_test)
            
            scaler_y = StandardScaler()
            y_train_scaled = scaler_y.fit_transform(y_train.values.reshape(-1, 1))
            y_test_scaled = scaler_y.transform(y_test.values.reshape(-1, 1))
            
            # Treinar modelos base
            base_models, best_params, features_clean = train_base_models(
                X_train_scaled=X_train_scaled,
                y_train_scaled=y_train_scaled,
                X_test_scaled=X_test_scaled,
                y_test=y_test.values,
                scaler_y=scaler_y,
                feature_names=features,
                source=f"fold_{fold}"
            )
            
            # Treinar stacking
            stacking_model, stacking_rmse, stacking_name = train_stacking_model(
                base_models=base_models,
                X_train_scaled=X_train_scaled,
                y_train_scaled=y_train_scaled,
                X_test_scaled=X_test_scaled,
                y_test=y_test.values,
                scaler_y=scaler_y,
                source=f"fold_{fold}"
            )
            
            if stacking_model is not None:
                # Fazer predições
                predictions = predict_models(base_models, stacking_model, X_test_scaled, scaler_y)
                
                # Calcular métricas
                stacking_metrics = calculate_metrics_stacking(
                    y_true=y_test.values,
                    y_pred=predictions["StackingRegressor"],
                    model_name="StackingRegressor",
                    source=f"fold_{fold}"
                )
                all_metrics.append(stacking_metrics)
                
        except Exception as e:
            print(f"    ⚠️ Erro no fold {fold}: {e}")
            continue
    
    # Calcular média das métricas entre folds
    if all_metrics:
        avg_metrics = calculate_average_metrics(all_metrics)
        return avg_metrics
    else:
        return {"rmse": None, "nrmse": None, "r2": None, "mape": None}
    
def stacking_cross_validation(df_complete: pd.DataFrame, test_fraction: float, target: str, n_splits: int = 5):
    """
    Executa validação cruzada para o stacking no dataset completo.
    """
    all_metrics = []
    
    # Preparar features
    df_transformed = transform(
        df=df_complete,
        coluna_original=target,
        coluna_nova=f"Feature_{target}",
        method="median"
    )
    
    # Features para modelo
    exclude_cols = {target, "Data", "mask_applied"}
    features = [c for c in df_transformed.columns if c not in exclude_cols]
    
    X = df_transformed[features].fillna(0)
    y = df_transformed[target]
    
    # Validação cruzada temporal
    tscv = TimeSeriesSplit(n_splits=min(n_splits, len(df_complete) // 2))
    
    for fold, (train_idx, test_idx) in enumerate(tscv.split(X)):
        print(f"    Fold {fold + 1}/{tscv.n_splits}")
        
        try:
            # Separar dados
            X_train, X_test = X.iloc[train_idx], X.iloc[test_idx]
            y_train, y_test = y.iloc[train_idx], y.iloc[test_idx]
            
            # Escalar dados
            scaler_X = StandardScaler()
            X_train_scaled = scaler_X.fit_transform(X_train)
            X_test_scaled = scaler_X.transform(X_test)
            
            scaler_y = StandardScaler()
            y_train_scaled = scaler_y.fit_transform(y_train.values.reshape(-1, 1))
            y_test_scaled = scaler_y.transform(y_test.values.reshape(-1, 1))
            
            # Treinar modelos base
            base_models, best_params, features_clean = train_base_models(
                X_train_scaled=X_train_scaled,
                y_train_scaled=y_train_scaled,
                X_test_scaled=X_test_scaled,
                y_test=y_test.values,
                scaler_y=scaler_y,
                feature_names=features,
                source=f"fold_{fold}"
            )
            
            # Treinar stacking
            stacking_model, stacking_rmse, stacking_name = train_stacking_model(
                base_models=base_models,
                X_train_scaled=X_train_scaled,
                y_train_scaled=y_train_scaled,
                X_test_scaled=X_test_scaled,
                y_test=y_test.values,
                scaler_y=scaler_y,
                source=f"fold_{fold}"
            )
            
            if stacking_model is not None:
                # Fazer predições
                predictions = predict_models(base_models, stacking_model, X_test_scaled, scaler_y)
                
                # Calcular métricas
                stacking_metrics = calculate_metrics_stacking(
                    y_true=y_test.values,
                    y_pred=predictions["StackingRegressor"],
                    model_name="StackingRegressor",
                    source=f"fold_{fold}"
                )
                all_metrics.append(stacking_metrics)
                
        except Exception as e:
            print(f"    ⚠️ Erro no fold {fold}: {e}")
            continue
    
    # Calcular média das métricas entre folds
    if all_metrics:
        avg_metrics = calculate_average_metrics(all_metrics)
        return avg_metrics
    else:
        return {"rmse": None, "nrmse": None, "r2": None, "mape": None}

def evaluate_stacking_cross_validation(df_complete: pd.DataFrame, fractions: list, target: str = "Vazao_BBR"):
    """
    Avalia stacking com validação cruzada usando dataset completo.
    """
    stacking_results = {}
    
    for frac in fractions:
        print(f"  [STACKING] Fração {frac}")
        
        # Para stacking, usar validação cruzada sem mask_applied
        cv_metrics = stacking_cross_validation(df_complete, test_fraction=frac, target=target)
        stacking_results[str(frac)] = cv_metrics
    
    return stacking_results

def pipeline_avaliacao_completa(file_path, fractions=[0.2, 0.25, 0.3, 0.35, 0.4, 0.45, 0.5]):
    """
    Pipeline completa de avaliação separada para baselines e stacking.
    CORREÇÃO: Agora o stacking é avaliado com máscaras iguais às baselines.
    """
    print(f"\n[AVALIANDO] {file_path.name}")
    df = pd.read_csv(file_path)
    source = file_path.stem.replace("_merged_largest_subseries", "").replace("_merged", "")
    target = "Vazao_BBR"
    
    results = {}
    
    # ========== PREPARAR DADOS ==========
    # Para BASELINES: usar maior sequência sem falhas
    df_preprocessed = preprocess_sequences(df, time_col="Data", freq_hours=6, col_validar=target, valor_invalido=-1)
    df_largest = get_largest_sequence(df_preprocessed)
    
    if df_largest.empty:
        print("  [SKIP] Nenhuma sequência válida para baselines")
        return None
    
    # Para STACKING: usar todos os dados válidos
    df_complete = get_complete_sequence_stacking(df, target)
    
    if len(df_complete) < 10:
        print("  [SKIP] Dados insuficientes para stacking")
        return None
    
    print(f"  [DADOS] Baseline: {len(df_largest)} amostras | Stacking: {len(df_complete)} amostras")
    
    # ========== AVALIAR BASELINES ==========
    print("  [AVALIAÇÃO BASELINES]")
    baseline_results = evaluate_baselines_single_run(df_largest, fractions, target)
    
    # ========== AVALIAR STACKING ==========
    print("  [AVALIAÇÃO STACKING]")
    # CORREÇÃO: Agora usa mesma lógica de máscaras que as baselines
    stacking_results = evaluate_stacking_with_masking(df_complete, fractions, target)
    
    # ========== COMBINAR RESULTADOS ==========
    for frac in fractions:
        frac_str = str(frac)
        results[frac_str] = {
            "baseline": baseline_results.get(frac_str, {}),
            "stacking": {
                "mean": {
                    "StackingRegressor": stacking_results.get(frac_str, {})
                }
            }
        }
    
    return {
        "source": source,
        "results": results,
        "dataset_sizes": {
            "baseline": len(df_largest),
            "stacking": len(df_complete)
        }
    }

In [39]:
def evaluate_stacking_with_masking(df_complete: pd.DataFrame, fractions: list, target: str = "Vazao_BBR"):
    """
    Avalia stacking aplicando máscaras de missing data (igual às baselines).
    CORREÇÃO: Agora usa máscaras para simular diferentes frações de missing.
    """
    stacking_results = {}
    
    for frac in fractions:
        print(f"  [STACKING] Fração {frac}")
        
        # Aplicar máscara (igual às baselines)
        df_masked = apply_mask(df_complete, test_fraction=frac, seed_data=42)
        
        # Avaliar stacking com esta máscara específica
        stacking_metrics = evaluate_stacking_single_run(df_masked, target)
        stacking_results[str(frac)] = stacking_metrics
    
    return stacking_results

def evaluate_stacking_single_run(df_masked: pd.DataFrame, target: str):
    """
    Avalia stacking em uma única execução com máscara específica - CORRIGIDA.
    """
    try:
        # VERIFICAÇÃO CRÍTICA: separar ANTES de transformar
        test_idx = df_masked[df_masked['mask_applied'] == 1].index
        train_idx = df_masked[df_masked['mask_applied'] == 0].index
        
        if len(train_idx) < 5 or len(test_idx) < 2:
            print(f"    ⚠️ Dados insuficientes: treino={len(train_idx)}, teste={len(test_idx)}")
            return {"rmse": None, "nrmse": None, "r2": None, "mape": None}
        
        print(f"    [SEPARAÇÃO] Treino: {len(train_idx)}, Teste: {len(test_idx)}")
        
        # Separar dados ANTES de qualquer feature engineering
        df_train = df_masked.loc[train_idx].copy()
        df_test = df_masked.loc[test_idx].copy()
        
        # Aplicar transformação SEPARADAMENTE para evitar vazamento
        df_train_transformed = transform_for_evaluation(
            df=df_train,
            coluna_original=target,
            coluna_nova=f"Feature_{target}",
            method="median"
        )
        
        df_test_transformed = transform_for_evaluation(
            df=df_test, 
            coluna_original=target,
            coluna_nova=f"Feature_{target}",
            method="median"
        )
        
        # Features para modelo
        exclude_cols = {target, "Data", "mask_applied"}
        features = [c for c in df_train_transformed.columns if c not in exclude_cols]
        
        X_train = df_train_transformed[features].fillna(0)
        X_test = df_test_transformed[features].fillna(0)
        y_train = df_train_transformed[target]
        y_test = df_test_transformed[target]
        
        # VERIFICAÇÃO DE VAZAMENTO
        train_indices = set(X_train.index)
        test_indices = set(X_test.index)
        overlap = train_indices.intersection(test_indices)
        
        if overlap:
            print(f"    ❌ CRÍTICO: {len(overlap)} amostras em treino e teste!")
            # Forçar recriação dos DataFrames para garantir separação
            X_train = X_train[~X_train.index.isin(test_indices)]
            y_train = y_train[~y_train.index.isin(test_indices)]
        
        # DEBUG: Verificar se há vazamento
        print(f"    [DEBUG] X_train: {X_train.shape}, X_test: {X_test.shape}")
        print(f"    [DEBUG] y_train range: {y_train.min():.2f}-{y_train.max():.2f}")
        print(f"    [DEBUG] y_test range: {y_test.min():.2f}-{y_test.max():.2f}")
        
        # Escalar dados
        scaler_X = StandardScaler()
        X_train_scaled = scaler_X.fit_transform(X_train)
        X_test_scaled = scaler_X.transform(X_test)
        
        scaler_y = StandardScaler()
        y_train_scaled = scaler_y.fit_transform(y_train.values.reshape(-1, 1))
        y_test_scaled = scaler_y.transform(y_test.values.reshape(-1, 1))
        
        # Treinar modelos base
        base_models, best_params, features_clean = train_base_models(
            X_train_scaled=X_train_scaled,
            y_train_scaled=y_train_scaled,
            X_test_scaled=X_test_scaled,
            y_test=y_test.values,
            scaler_y=scaler_y,
            feature_names=features,
            source=f"stacking_eval"
        )
        
        if not base_models:
            print("    ⚠️ Nenhum modelo base treinado")
            return {"rmse": None, "nrmse": None, "r2": None, "mape": None}
        
        # Ajustar X_test para features limpas
        feature_indices = [features.index(f) for f in features_clean]
        X_test_scaled_clean = X_test_scaled[:, feature_indices]
        
        # Treinar stacking
        stacking_model, stacking_rmse, stacking_name = train_stacking_model(
            base_models=base_models,
            X_train_scaled=X_train_scaled[:, feature_indices],
            y_train_scaled=y_train_scaled,
            X_test_scaled=X_test_scaled_clean,
            y_test=y_test.values,
            scaler_y=scaler_y,
            source=f"stacking_eval"
        )
        
        if stacking_model is None:
            print("    ⚠️ Stacking não pôde ser treinado")
            return {"rmse": None, "nrmse": None, "r2": None, "mape": None}
        
        # Fazer predições
        predictions = predict_models(base_models, stacking_model, X_test_scaled_clean, scaler_y)
        
        if "StackingRegressor" in predictions:
            y_pred = predictions["StackingRegressor"]
            y_true = y_test.values
            
            # DEBUG: Verificar se predições são realistas
            print(f"    [DEBUG PREDIÇÕES]")
            print(f"      y_true[:5]: {y_true[:5]}")
            print(f"      y_pred[:5]: {y_pred[:5]}")
            
            # Verificar se há overfitting extremo
            if np.allclose(y_pred, y_true, rtol=0.01):
                print("    ⚠️ ALERTA: Predições quase idênticas aos valores reais!")
            
            # Calcular métricas
            stacking_metrics = calculate_metrics_stacking(
                y_true=y_true,
                y_pred=y_pred,
                model_name="StackingRegressor",
                source=f"stacking_eval"
            )
            
            print(f"    ✅ Stacking RMSE: {stacking_metrics['rmse']}, R²: {stacking_metrics['r2']}")
            return stacking_metrics
        else:
            print("    ⚠️ Nenhuma predição do Stacking")
            return {"rmse": None, "nrmse": None, "r2": None, "mape": None}
            
    except Exception as e:
        print(f"    ✗ Erro na avaliação do stacking: {e}")
        import traceback
        traceback.print_exc()
        return {"rmse": None, "nrmse": None, "r2": None, "mape": None}

In [40]:
# ========== FUNÇÕES DE IMPUTAÇÃO E EXECUÇÃO ==========

def save_partial_results(all_results, json_path="metrics_summary_unfair.json"):
    with open(json_path, "w") as f:
        json.dump(all_results, f, indent=4)

def imputar_e_salvar(source, df_original, out_dir):
    """
    Imputa dados usando baselines e stacking, salvando os resultados.
    """
    print(f"\n[IMPUTANDO] {source}")
    target = "Vazao_BBR"
    cols_keep = ["Data", "Atraso(ms)", "Hop_count", "Bottleneck", "Vazao_BBR", "mask_applied"]
    
    out_dir = Path(out_dir)
    out_dir.mkdir(parents=True, exist_ok=True)
    
    # Criar DataFrame para imputação
    df_imputation = df_original.copy()
    
    # CORREÇÃO: Criar mask_applied identificando valores que precisam ser imputados
    df_imputation["mask_applied"] = df_imputation[target].apply(
        lambda x: 1 if pd.isna(x) or x == -1 else 0
    )
    
    missing_count = df_imputation["mask_applied"].sum()
    print(f"  [INFO] {missing_count} valores a serem imputados")
    
    if missing_count == 0:
        print(f"  [SKIP] Nenhum valor para imputar em {source}")
        return
    
    # ============== BASELINES ==============
    print(f"  [BASELINES] Calculando imputações baseline...")
    
    baseline_methods = {
        'mean': lambda df: df[target].replace(-1, np.nan).fillna(df[target].replace(-1, np.nan).mean()),
        'median': lambda df: df[target].replace(-1, np.nan).fillna(df[target].replace(-1, np.nan).median()),
        'knn': lambda df: KNNImputer(n_neighbors=4).fit_transform(
            df[[target]].replace(-1, np.nan)
        ).ravel(),
        'ffill': lambda df: df[target].replace(-1, np.nan).ffill().bfill(),
        'bfill': lambda df: df[target].replace(-1, np.nan).bfill().ffill()
    }
    
    for method_name, impute_func in baseline_methods.items():
        try:
            df_imp = df_imputation.copy()
            df_imp[target] = impute_func(df_imp)
            
            out_path = out_dir / f"{source}_baseline_{method_name}.csv"
            df_imp[cols_keep].to_csv(out_path, index=False)
            print(f"    ✓ Baseline {method_name}: {out_path.name}")
        except Exception as e:
            print(f"    ✗ Erro em baseline {method_name}: {e}")
    
    # ============== STACKING ==============
    print(f"  [STACKING] Preparando features e treinando modelo...")
    
    try:
        # Usar a nova função transform para imputação
        df_feat = transform_imputation(
            df=df_imputation,
            coluna_original=target,
            coluna_nova=f"Feature_{target}",
            method="median"
        )
        
        # Garantir que mask_applied está preservada
        df_feat["mask_applied"] = df_imputation["mask_applied"]
        
        # Preparar dados
        exclude_cols = {target, "Data", "mask_applied"}
        features = [c for c in df_feat.columns if c not in exclude_cols]
        X = df_feat[features].fillna(0)
        y = df_feat[target]
        
        # Índices válidos (não-missing) para treino
        mask_valid = (y != -1) & (~y.isna())
        
        if mask_valid.sum() >= 5:
            print(f"    [TREINAMENTO] {mask_valid.sum()} amostras válidas para treino")
            
            # Escalar X
            scaler_X = StandardScaler()
            X_clean = X.loc[mask_valid].copy()
            X_clean.replace([np.inf, -np.inf], np.nan, inplace=True)
            X_clean.fillna(0, inplace=True)
            X_scaled = scaler_X.fit_transform(X_clean)
            
            # Escalar y
            scaler_y = StandardScaler()
            y_valid = y.loc[mask_valid].values
            y_scaled = scaler_y.fit_transform(y_valid.reshape(-1, 1))
            
            # Treinar modelos base
            base_models, base_params, features_clean = train_base_models(
                X_train_scaled=X_scaled,
                y_train_scaled=y_scaled,
                X_test_scaled=X_scaled,
                y_test=y_valid,
                scaler_y=scaler_y,
                feature_names=list(X.columns),
                source=source
            )
            
            if not base_models:
                print("    ⚠️ Nenhum modelo base treinado com sucesso")
                return
            
            # AJUSTAR X_scaled para usar apenas features limpas
            feature_indices = [list(X.columns).index(f) for f in features_clean]
            X_scaled_clean = X_scaled[:, feature_indices]
            
            # Treinar stacking
            stacking_model, stacking_rmse, stacking_name = train_stacking_model(
                base_models=base_models,
                X_train_scaled=X_scaled_clean,
                y_train_scaled=y_scaled,
                X_test_scaled=X_scaled_clean,
                y_test=y_valid,
                scaler_y=scaler_y,
                source=source
            )
            
            if stacking_model is None:
                print("    ⚠️ Stacking não pôde ser treinado")
                return
            
            # Imputar valores faltantes (onde mask_applied == 1)
            missing_idx = df_feat[df_feat["mask_applied"] == 1].index
            
            if len(missing_idx) > 0:
                print(f"    [IMPUTAÇÃO] Imputando {len(missing_idx)} valores com Stacking...")
                
                X_missing = X.loc[missing_idx].copy()
                X_missing.replace([np.inf, -np.inf], np.nan, inplace=True)
                X_missing.fillna(0, inplace=True)
                X_missing_scaled = scaler_X.transform(X_missing)
                
                # Ajustar para features limpas
                X_missing_scaled_clean = X_missing_scaled[:, feature_indices]
                
                # Fazer predições
                preds = predict_models(base_models, stacking_model, X_missing_scaled_clean, scaler_y)
                
                if "StackingRegressor" in preds:
                    # Aplicar imputações
                    df_feat.loc[missing_idx, target] = preds["StackingRegressor"]
                    print(f"    ✓ Imputados {len(missing_idx)} valores com Stacking (meta-modelo: {stacking_name})")
                    
                    # Salvar resultado
                    out_path = out_dir / f"{source}_stacking.csv"
                    df_feat[cols_keep].to_csv(out_path, index=False)
                    print(f"    ✓ Stacking: {out_path.name}")
                else:
                    print("    ⚠️ Nenhuma predição do Stacking disponível")
            else:
                print(f"    ⚠️ Nenhum valor para imputar encontrado")
        else:
            print(f"    ✗ Dados insuficientes para treinar Stacking (apenas {mask_valid.sum()} amostras válidas)")
            
    except Exception as e:
        print(f"    ✗ Erro no Stacking: {e}")
        import traceback
        traceback.print_exc()
    
    print(f"[CONCLUÍDO IMPUTAÇÃO] {source}\n")

def imputacao_inteligente(source, df_original, all_results, out_dir):
    """
    Decide se deve imputar baseado nos resultados e executa a imputação.
    """
    print(f"\n[ANALISANDO IMPUTAÇÃO] {source}")
    
    # Verificar se stacking foi melhor na maioria das frações
    frac_vitorias = 0
    total_frac = 0
    
    if source not in all_results:
        print("  [SKIP] Nenhum resultado encontrado para esta fonte")
        return
    
    source_results = all_results[source]
    
    for frac, data in source_results.items():
        baseline_data = data.get("baseline", {})
        stacking_data = data.get("stacking", {}).get("mean", {}).get("StackingRegressor", {})
        
        if baseline_data and stacking_data and stacking_data.get("rmse") is not None:
            total_frac += 1
            
            # Comparar RMSE do stacking com a melhor baseline
            baseline_rmses = [metrics["rmse"] for metrics in baseline_data.values() if metrics["rmse"] is not None]
            if baseline_rmses:
                best_baseline_rmse = min(baseline_rmses)
                stacking_rmse = stacking_data["rmse"]
                
                if stacking_rmse < best_baseline_rmse:
                    frac_vitorias += 1
    
    # Critério: stacking deve ser melhor em pelo menos 50% das frações
    if total_frac > 0 and (frac_vitorias / total_frac) >= 0.5:
        print(f"  ✅ Stacking melhor em {frac_vitorias}/{total_frac} frações - IMPUTANDO")
        imputar_e_salvar(source, df_original, out_dir)
    else:
        print(f"  ❌ Stacking melhor em apenas {frac_vitorias}/{total_frac} frações - NÃO IMPUTAR")

# ========== EXECUÇÃO PRINCIPAL ==========

# Lista de arquivos
data_path = Path("../../datasets/multivariada-post-process")
csv_files = list(data_path.glob("*_merged.csv"))

fractions = [0.2, 0.25, 0.3, 0.35, 0.4, 0.45, 0.5]
all_results = {}
out_dir = Path("../../datasets/multivariada-results/imputed_series_selective_unfair")
out_dir.mkdir(exist_ok=True, parents=True)

print(f"[INICIANDO AVALIAÇÃO] {len(csv_files)} arquivos")

for file_path in csv_files:
    try:
        # Executar avaliação completa
        resultado = pipeline_avaliacao_completa(file_path, fractions)
        
        if resultado is not None:
            source = resultado["source"]
            all_results[source] = resultado["results"]
            
            # Salvar resultados parciais
            save_partial_results(all_results, json_path=out_dir / "metrics_summary_unfair.json")
            
            # Decidir sobre imputação
            imputacao_inteligente(source, pd.read_csv(file_path), all_results, out_dir)
            
    except Exception as e:
        print(f"❌ Erro processando {file_path.name}: {e}")
        continue

print(f"\n[CONCLUÍDO] Processamento finalizado!")

[INICIANDO AVALIAÇÃO] 615 arquivos

[AVALIANDO] ac-am_merged.csv
[STACKING] Dataset completo: 1326 amostras válidas
  [DADOS] Baseline: 29 amostras | Stacking: 1326 amostras
  [AVALIAÇÃO BASELINES]
  [BASELINE] Fração 0.2
      Máscara: 5/29 amostras (20.0%)
  [BASELINE] Fração 0.25
      Máscara: 7/29 amostras (25.0%)
  [BASELINE] Fração 0.3
      Máscara: 8/29 amostras (30.0%)
  [BASELINE] Fração 0.35
      Máscara: 10/29 amostras (35.0%)
  [BASELINE] Fração 0.4
      Máscara: 11/29 amostras (40.0%)
  [BASELINE] Fração 0.45
      Máscara: 13/29 amostras (45.0%)
  [BASELINE] Fração 0.5
      Máscara: 14/29 amostras (50.0%)
  [AVALIAÇÃO STACKING]
  [STACKING] Fração 0.2
      Máscara: 265/1326 amostras (20.0%)
    [SEPARAÇÃO] Treino: 1061, Teste: 265
    [DEBUG] X_train: (1061, 24), X_test: (265, 24)
    [DEBUG] y_train range: 52128.00-929877708.00
    [DEBUG] y_test range: 891291.00-932605546.00
    📊 Features: 24 → 24 (após remoção de NaN)
    🔧 Otimizando XGBRegressor...
    ✅ XGBRe

Traceback (most recent call last):
  File "C:\Users\LARCES_MALU\AppData\Local\Temp\ipykernel_21132\299564297.py", line 81, in evaluate_stacking_single_run
    X_train_scaled = scaler_X.fit_transform(X_train)
                     ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\LARCES_MALU\Desktop\ENHANCED-IMPUTATION-PREDICTION\.venv\Lib\site-packages\sklearn\utils\_set_output.py", line 316, in wrapped
    data_to_wrap = f(self, X, *args, **kwargs)
                   ^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\LARCES_MALU\Desktop\ENHANCED-IMPUTATION-PREDICTION\.venv\Lib\site-packages\sklearn\base.py", line 894, in fit_transform
    return self.fit(X, **fit_params).transform(X)
           ^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\LARCES_MALU\Desktop\ENHANCED-IMPUTATION-PREDICTION\.venv\Lib\site-packages\sklearn\preprocessing\_data.py", line 907, in fit
    return self.partial_fit(X, y, sample_weight)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\LARCES_MALU\Desktop\


[ANALISANDO IMPUTAÇÃO] ac-pa
  ❌ Stacking melhor em apenas 0/0 frações - NÃO IMPUTAR

[AVALIANDO] ac-pb_merged.csv
[STACKING] Dataset completo: 1313 amostras válidas
  [DADOS] Baseline: 28 amostras | Stacking: 1313 amostras
  [AVALIAÇÃO BASELINES]
  [BASELINE] Fração 0.2
      Máscara: 5/28 amostras (20.0%)
  [BASELINE] Fração 0.25
      Máscara: 7/28 amostras (25.0%)
  [BASELINE] Fração 0.3
      Máscara: 8/28 amostras (30.0%)
  [BASELINE] Fração 0.35
      Máscara: 9/28 amostras (35.0%)
  [BASELINE] Fração 0.4
      Máscara: 11/28 amostras (40.0%)
  [BASELINE] Fração 0.45
      Máscara: 12/28 amostras (45.0%)
  [BASELINE] Fração 0.5
      Máscara: 14/28 amostras (50.0%)
  [AVALIAÇÃO STACKING]
  [STACKING] Fração 0.2
      Máscara: 262/1313 amostras (20.0%)
    [SEPARAÇÃO] Treino: 1051, Teste: 262
    [DEBUG] X_train: (1051, 24), X_test: (262, 24)
    [DEBUG] y_train range: 54958720.00-933957817.00
    [DEBUG] y_test range: 117099852.50-930350823.00
    📊 Features: 24 → 24 (após remo

Traceback (most recent call last):
  File "C:\Users\LARCES_MALU\AppData\Local\Temp\ipykernel_21132\299564297.py", line 81, in evaluate_stacking_single_run
    X_train_scaled = scaler_X.fit_transform(X_train)
                     ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\LARCES_MALU\Desktop\ENHANCED-IMPUTATION-PREDICTION\.venv\Lib\site-packages\sklearn\utils\_set_output.py", line 316, in wrapped
    data_to_wrap = f(self, X, *args, **kwargs)
                   ^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\LARCES_MALU\Desktop\ENHANCED-IMPUTATION-PREDICTION\.venv\Lib\site-packages\sklearn\base.py", line 894, in fit_transform
    return self.fit(X, **fit_params).transform(X)
           ^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\LARCES_MALU\Desktop\ENHANCED-IMPUTATION-PREDICTION\.venv\Lib\site-packages\sklearn\preprocessing\_data.py", line 907, in fit
    return self.partial_fit(X, y, sample_weight)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "c:\Users\LARCES_MALU\Desktop\

    [DEBUG] X_train: (746, 24), X_test: (609, 24)
    [DEBUG] y_train range: 481611534.00-937268157.00
    [DEBUG] y_test range: 209453380.00-936014642.00
    ✗ Erro na avaliação do stacking: Input X contains infinity or a value too large for dtype('float64').
  [STACKING] Fração 0.5
      Máscara: 677/1355 amostras (50.0%)
    [SEPARAÇÃO] Treino: 678, Teste: 677
    [DEBUG] X_train: (678, 24), X_test: (677, 24)
    [DEBUG] y_train range: 481611534.00-936434167.00
    [DEBUG] y_test range: 209453380.00-937268157.00
    ✗ Erro na avaliação do stacking: Input X contains infinity or a value too large for dtype('float64').

[ANALISANDO IMPUTAÇÃO] am-ap
  ❌ Stacking melhor em apenas 0/0 frações - NÃO IMPUTAR

[AVALIANDO] am-ba_merged.csv
[STACKING] Dataset completo: 1231 amostras válidas
  [DADOS] Baseline: 28 amostras | Stacking: 1231 amostras
  [AVALIAÇÃO BASELINES]
  [BASELINE] Fração 0.2
      Máscara: 5/28 amostras (20.0%)
  [BASELINE] Fração 0.25
      Máscara: 7/28 amostras (25.0%)
 

...

  [BASELINE] Fração 0.35
      Máscara: 2/8 amostras (35.0%)
  [BASELINE] Fração 0.4
      Máscara: 3/8 amostras (40.0%)
  [BASELINE] Fração 0.45
      Máscara: 3/8 amostras (45.0%)
  [BASELINE] Fração 0.5
      Máscara: 4/8 amostras (50.0%)
  [AVALIAÇÃO STACKING]
  [STACKING] Fração 0.2
      Máscara: 40/200 amostras (20.0%)
    [SEPARAÇÃO] Treino: 160, Teste: 40
    [DEBUG] X_train: (160, 24), X_test: (40, 24)
    [DEBUG] y_train range: 589819475.00-913415421.00
    [DEBUG] y_test range: 846883888.00-909976183.00
    📊 Features: 24 → 24 (após remoção de NaN)
    🔧 Otimizando XGBRegressor...
    ✅ XGBRegressor - RMSE: 12.60M
    🔧 Otimizando RandomForestRegressor...
    ✅ RandomForestRegressor - RMSE: 13.86M
    🔧 Otimizando GradientBoostingRegressor...
    ✅ GradientBoostingRegressor - RMSE: 11.56M
    🔧 Otimizando KNeighborsRegressor...
    ✅ KNeighborsRegressor - RMSE: 15.94M
    🔧 Otimizando ElasticNet...
    ✅ ElasticNet - RMSE: 0.30M
    🎯 Stacking (Ridge) - RMSE: 0.23M
    [DEB

c:\Users\LARCES_MALU\Desktop\ENHANCED-IMPUTATION-PREDICTION\.venv\Lib\site-packages\sklearn\metrics\_regression.py:1283: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\LARCES_MALU\Desktop\ENHANCED-IMPUTATION-PREDICTION\.venv\Lib\site-packages\sklearn\metrics\_regression.py:1283: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\LARCES_MALU\Desktop\ENHANCED-IMPUTATION-PREDICTION\.venv\Lib\site-packages\sklearn\metrics\_regression.py:1283: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\LARCES_MALU\Desktop\ENHANCED-IMPUTATION-PREDICTION\.venv\Lib\site-packages\sklearn\metrics\_regression.py:1283: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users

  [BASELINE] Fração 0.35
      Máscara: 2/8 amostras (35.0%)
  [BASELINE] Fração 0.4
      Máscara: 3/8 amostras (40.0%)
  [BASELINE] Fração 0.45
      Máscara: 3/8 amostras (45.0%)
  [BASELINE] Fração 0.5
      Máscara: 4/8 amostras (50.0%)
  [AVALIAÇÃO STACKING]
  [STACKING] Fração 0.2
      Máscara: 70/351 amostras (20.0%)
    [SEPARAÇÃO] Treino: 281, Teste: 70
    [DEBUG] X_train: (281, 24), X_test: (70, 24)
    [DEBUG] y_train range: 10852769.00-905181647.00
    [DEBUG] y_test range: 195297589.50-890138703.00
    📊 Features: 24 → 24 (após remoção de NaN)
    🔧 Otimizando XGBRegressor...
    ✅ XGBRegressor - RMSE: 17.87M
    🔧 Otimizando RandomForestRegressor...
    ✅ RandomForestRegressor - RMSE: 21.00M
    🔧 Otimizando GradientBoostingRegressor...
    ✅ GradientBoostingRegressor - RMSE: 14.39M
    🔧 Otimizando KNeighborsRegressor...
    ✅ KNeighborsRegressor - RMSE: 52.47M
    🔧 Otimizando ElasticNet...
    ✅ ElasticNet - RMSE: 6.19M
    🎯 Stacking (Ridge) - RMSE: 1.85M
    [DEBU

c:\Users\LARCES_MALU\Desktop\ENHANCED-IMPUTATION-PREDICTION\.venv\Lib\site-packages\sklearn\metrics\_regression.py:1283: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\LARCES_MALU\Desktop\ENHANCED-IMPUTATION-PREDICTION\.venv\Lib\site-packages\sklearn\metrics\_regression.py:1283: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\LARCES_MALU\Desktop\ENHANCED-IMPUTATION-PREDICTION\.venv\Lib\site-packages\sklearn\metrics\_regression.py:1283: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users\LARCES_MALU\Desktop\ENHANCED-IMPUTATION-PREDICTION\.venv\Lib\site-packages\sklearn\metrics\_regression.py:1283: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
c:\Users

  [BASELINE] Fração 0.25
      Máscara: 2/9 amostras (25.0%)
  [BASELINE] Fração 0.3
      Máscara: 2/9 amostras (30.0%)
  [BASELINE] Fração 0.35
      Máscara: 3/9 amostras (35.0%)
  [BASELINE] Fração 0.4
      Máscara: 3/9 amostras (40.0%)
  [BASELINE] Fração 0.45
      Máscara: 4/9 amostras (45.0%)
  [BASELINE] Fração 0.5
      Máscara: 4/9 amostras (50.0%)
  [AVALIAÇÃO STACKING]
  [STACKING] Fração 0.2
      Máscara: 53/267 amostras (20.0%)
    [SEPARAÇÃO] Treino: 214, Teste: 53
    [DEBUG] X_train: (214, 24), X_test: (53, 24)
    [DEBUG] y_train range: 842584129.00-986069284.00
    [DEBUG] y_test range: 769847641.00-975805459.00
    📊 Features: 24 → 24 (após remoção de NaN)
    🔧 Otimizando XGBRegressor...
    ✅ XGBRegressor - RMSE: 3.89M
    🔧 Otimizando RandomForestRegressor...
    ✅ RandomForestRegressor - RMSE: 3.74M
    🔧 Otimizando GradientBoostingRegressor...
    ✅ GradientBoostingRegressor - RMSE: 2.97M
    🔧 Otimizando KNeighborsRegressor...
    ✅ KNeighborsRegressor - RM